# Eat Safe, Love

## Part 1: Database and Jupyter Notebook Set Up

Import the data provided in the `establishments.json` file from your Terminal. Name the database `uk_food` and the collection `establishments`.

Within this markdown cell, copy the line of text you used to import the data from your Terminal. This way, future analysts will be able to repeat your process.

e.g.: Import the dataset with mongoimport --type json -d uk_food -c establishments --drop --jsonArray establishments.json

In [1]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint

In [2]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [3]:
# confirm that our new database was created
print(mongo.list_database_names())

['admin', 'classDB', 'config', 'epa', 'fruits_db', 'local', 'met', 'petsitly_marketing', 'travel_db', 'uk_food']


In [5]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [6]:
# review the collections in our new database
pprint(db.list_collection_names())

['establishments']


In [8]:
# review a document in the establishments collection
pprint(db.establishments.find_one())

{'AddressLine1': 'The Pines Garden',
 'AddressLine2': 'Beach Road',
 'AddressLine3': 'St Margarets Bay',
 'AddressLine4': 'Kent',
 'BusinessName': 'The Tea Room',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4587.362402580997,
 'FHRSID': 551803,
 'LocalAuthorityBusinessID': 'PI/000070948',
 'LocalAuthorityCode': '182',
 'LocalAuthorityEmailAddress': 'publicprotection@dover.gov.uk',
 'LocalAuthorityName': 'Dover',
 'LocalAuthorityWebSite': 'http://www.dover.gov.uk/',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT15 6DZ',
 'RatingDate': '2021-08-17T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': '5',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('64bf2451f553f0156cb2ebba'),
 'geocode': {'latitude': '51.148133', 'longitude': '1.383298'},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/551803',
            'rel': 'self'}],
 'meta': {'dataSource': None,
          'extractDate':

In [29]:
# assign the collection to a variable
establishments = db.establishments

## Part 2: Update the Database

1. An exciting new halal restaurant just opened in Greenwich, but hasn't been rated yet. The magazine has asked you to include it in your analysis. Add the following restaurant "Penang Flavours" to the database.

In [30]:
# Create a dictionary for the new restaurant data
new_res = {
    "BusinessName":"Penang Flavours",
    "BusinessType":"Restaurant/Cafe/Canteen",
    "BusinessTypeID":"",
    "AddressLine1":"Penang Flavours",
    "AddressLine2":"146A Plumstead Rd",
    "AddressLine3":"London",
    "AddressLine4":"",
    "PostCode":"SE18 7DY",
    "Phone":"",
    "LocalAuthorityCode":"511",
    "LocalAuthorityName":"Greenwich",
    "LocalAuthorityWebSite":"http://www.royalgreenwich.gov.uk",
    "LocalAuthorityEmailAddress":"health@royalgreenwich.gov.uk",
    "scores":{
        "Hygiene":"",
        "Structural":"",
        "ConfidenceInManagement":""
    },
    "SchemeType":"FHRS",
    "geocode":{
        "longitude":"0.08384000",
        "latitude":"51.49014200"
    },
    "RightToReply":"",
    "Distance":4623.9723280747176,
    "NewRatingPending":True
}

In [31]:
# Insert the new restaurant into the collection
establishments.insert_one(new_res)

In [32]:
# Check that the new restaurant was inserted
query = {"BusinessName": "Penang Flavours"}
results = establishments.find(query)
for result in results:
    pprint(result)

{'AddressLine1': 'Penang Flavours',
 'AddressLine2': '146A Plumstead Rd',
 'AddressLine3': 'London',
 'AddressLine4': '',
 'BusinessName': 'Penang Flavours',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': '',
 'Distance': 4623.972328074718,
 'LocalAuthorityCode': '511',
 'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk',
 'LocalAuthorityName': 'Greenwich',
 'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk',
 'NewRatingPending': True,
 'Phone': '',
 'PostCode': 'SE18 7DY',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('64bf26f71030b8625062478e'),
 'geocode': {'latitude': '51.49014200', 'longitude': '0.08384000'},
 'scores': {'ConfidenceInManagement': '', 'Hygiene': '', 'Structural': ''}}
{'AddressLine1': 'Penang Flavours',
 'AddressLine2': '146A Plumstead Rd',
 'AddressLine3': 'London',
 'AddressLine4': '',
 'BusinessName': 'Penang Flavours',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': '',
 'Distance': 4623.972328074

2. Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the `BusinessTypeID` and `BusinessType` fields.

In [37]:
# Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the BusinessTypeID and BusinessType fields
query = {'BusinessType': 'Restaurant/Cafe/Canteen'}
fields = {'BusinessTypeID':1, 'BusinessType':1}
required_ID = establishments.find_one(query, fields)
print(required_ID)

{'_id': ObjectId('64bf2451f553f0156cb2ebba'), 'BusinessType': 'Restaurant/Cafe/Canteen', 'BusinessTypeID': 1}


3. Update the new restaurant with the `BusinessTypeID` you found.

In [38]:
# Update the new restaurant with the correct BusinessTypeID
establishments.update_one(
    {"BusinessName":"Penang Flavours"},
    {'$set':
     {'BusinessTypeID': required_ID['BusinessTypeID']}
    }
)

In [39]:
# Confirm that the new restaurant was updated
query = {"BusinessName":"Penang Flavours"}
fields = {'BusinessTypeID':1}
results = establishments.find(query, fields)
for result in results:
    print(result)

{'_id': ObjectId('64bf26f71030b8625062478e'), 'BusinessTypeID': 1}
{'_id': ObjectId('64bf2b071030b8625062478f'), 'BusinessTypeID': ''}


4. The magazine is not interested in any establishments in Dover, so check how many documents contain the Dover Local Authority. Then, remove any establishments within the Dover Local Authority from the database, and check the number of documents to ensure they were deleted.

In [40]:
# Find how many documents have LocalAuthorityName as "Dover"
query = {'LocalAuthorityName' : 'Dover'}
docs_dover = establishments.count_documents(query)
print(f"Number of establishments in Dover: {docs_dover}")

Number of establishments in Dover: 994


In [41]:
# Delete all documents where LocalAuthorityName is "Dover"
establishments.delete_many(query)

In [42]:
# Check if any remaining documents include Dover
docs_dover_recheck = establishments.count_documents(query)
print(f"Number of establishments in Dover: {docs_dover_recheck}")

Number of establishments in Dover: 0


In [43]:
# Check that other documents remain with 'find_one'
check = establishments.find_one()
pprint(check)

{'AddressLine1': 'East Cliff Pavilion',
 'AddressLine2': 'Wear Bay Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'BusinessName': 'The Pavilion',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4591.765489457773,
 'FHRSID': 1043695,
 'LocalAuthorityBusinessID': 'PI/000073616',
 'LocalAuthorityCode': '188',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT19 6BL',
 'RatingDate': '2018-04-04T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': '5',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('64bf2451f553f0156cb2eea1'),
 'geocode': {'latitude': '51.083812', 'longitude': '1.195625'},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1043695',
            'rel': 'self'}],
 'meta': {'dataSource': 

5. Some of the number values are stored as strings, when they should be stored as numbers.

Use `update_many` to convert `latitude` and `longitude` to decimal numbers.

In [45]:
# Change the data type from String to Decimal for longitude and latitude
establishments.update_many({}, [ {'$set':{ "geocode.longitude" : {'$toDouble': "$geocode.longitude"}}} ])

establishments.update_many({}, [ {'$set':{ "geocode.latitude" : {'$toDouble': "$geocode.latitude"}}} ])

#checking if all have been converted
query = {}
fields = {'BusinessName': 1, 'geocode.longitude': 1, 'geocode.latitude': 1}

# Capture the results to a variable
check_results = establishments.find(query, fields)

# Pretty print the results
for each_result in check_results:
    pprint(each_result)

{'BusinessName': 'The Pavilion',
 '_id': ObjectId('64bf2451f553f0156cb2eea1'),
 'geocode': {'latitude': 51.083812, 'longitude': 1.195625}}
{'BusinessName': 'Wear Bay Bowls Club',
 '_id': ObjectId('64bf2451f553f0156cb2eea2'),
 'geocode': {'latitude': 51.086058, 'longitude': 1.196408}}
{'BusinessName': 'St Marys COE (aided) Primary School',
 '_id': ObjectId('64bf2451f553f0156cb2eea3'),
 'geocode': {'latitude': 51.085797, 'longitude': 1.194762}}
{'BusinessName': 'The Ship',
 '_id': ObjectId('64bf2451f553f0156cb2eea5'),
 'geocode': {'latitude': 51.08084, 'longitude': 1.188537}}
{'BusinessName': 'The Ships Galley',
 '_id': ObjectId('64bf2451f553f0156cb2eea7'),
 'geocode': {'latitude': 51.08084, 'longitude': 1.188537}}
{'BusinessName': 'Mariner',
 '_id': ObjectId('64bf2451f553f0156cb2eea8'),
 'geocode': {'latitude': 51.08084, 'longitude': 1.188537}}
{'BusinessName': 'Folkestone Trawlers Shop',
 '_id': ObjectId('64bf2451f553f0156cb2eea9'),
 'geocode': {'latitude': 51.08084, 'longitude': 1.188